# How to import OpenQASM

**Importing OpenQASM from external files to Python**

Submitting circuits to Fire Opal requires the circuits to be formatted as [OpenQASM](https://openqasm.com/) strings. This notebook demonstrates how to import OpenQASM strings from external files for use with Fire Opal.

In this guide, you will learn how to:
1. Extract OpenQASM strings from files.
1. Validate the circuits to check for errors.

### 1. Import packages and define helper functions

In [1]:
import os
import fireopal as fo

In order to read the files, we define a helper function to pull all OpenQASM strings from a file, and specify the directory in which the files are found.

In [2]:
def extract_qasm(lines: list[str], starting_idx: int) -> tuple[str, int]:
    "Extract the next QASM string from the file."
    qasm_array = []
    line_data = ""
    line_idx = starting_idx

    # Find the starting line.
    while "OPENQASM" not in line_data and line_idx < len(lines):
        line_data = lines[line_idx]
        line_idx += 1

    if line_idx == len(lines):
        return None, line_idx

    qasm_array.append(line_data)

    # Keep adding lines until we see a new line.
    while lines[line_idx] != "\n":
        qasm_array.append(lines[line_idx])
        line_idx += 1

    return ("".join(qasm_array), line_idx)

In [ ]:
circuit_directory = "../relative/path/to/circuits"  # the relative path from this notebook to your file(s)
circuit_filenames = [
    filename
    for filename in os.listdir(circuit_directory)
    if filename.endswith((".txt", ".qasm"))
]

### 2. Read OpenQASM strings from file(s)

Next, we create a list of OpenQASM strings from the files specified above.

In [ ]:
circuit_list = []
for filename in circuit_filenames:
    with open(circuit_directory + filename, "r") as filehandle:
        lines = filehandle.readlines()

    line_idx = 0
    while line_idx < len(lines):
        qasm_str, line_idx = extract_qasm(lines, line_idx)
        if qasm_str is not None:
            circuit_list.append(qasm_str)

### 3. Validate imported strings for use with Fire Opal

Finally, we ensure the imported strings are valid OpenQASM strings that can be executed with Fire Opal using the `validate` function.

In [ ]:
# Enter your IBM token here.
token = "your_IBM_token"

# These are the properties for the publicly available provider for IBM backends.
# If you have access to a private provider and wish to use it, replace these values.
hub = "ibm-q"
group = "open"
project = "main"

credentials = fo.credentials.make_credentials_for_ibmq(
    token=token, hub=hub, group=group, project=project
)

# Enter your desired IBM backend here.
backend_name = "desired_backend"

validate_results = fo.validate(
    circuits=circuit_list, credentials=credentials, backend_name=backend_name
)

In [ ]:
print(f"Number of circuits validated: {len(circuit_list)}")
print(f"Number of circuit errors found: {len(validate_results['results'])}")

The package versions below were used to produce this notebook.

In [4]:
from fireopal import print_package_versions

print_package_versions()

| Package               | Version |
| --------------------- | ------- |
| Python                | 3.11.0  |
| networkx              | 2.8.8   |
| numpy                 | 1.26.2  |
| sympy                 | 1.12    |
| fire-opal             | 6.7.0   |
| qctrl-workflow-client | 2.2.0   |
